In [53]:
# import libraries
import numpy as np
import plotly.express as px 
import skimage as ski
from skimage.color import rgb2hsv, hsv2rgb

# Function that converts a hsv image into a gray_scale hsv image
def gray_scale(hsv):
    hsv_grayScale = np.copy(hsv)
    hsv_grayScale[:, :, 1] = 0  
    return hsv_grayScale

def createMaskInRange(hsv, lower_bound, upper_bound):
    mask = np.all((hsv >= lower_bound) & (hsv <= upper_bound), axis=2) # provare a farla direttamente 3d instead of 2d, ma nel caso bisogna modificare anche la applyMask
    return mask

def createInvMask(maskToInv):
    invMask = np.logical_not(maskToInv)
    return invMask

def applyMask(img, mask):
    mask = mask.astype('uint8')
    mask = np.repeat(mask, 3, axis=1)
    mask = np.reshape(mask, img.shape)
    res = img * mask
    return res

def convertTo255(img):
    img = img * 255
    img = img.astype('uint8')
    return img

def applyFilterToImg(img, lower_bound, upper_bound):
    # convert the image in HSV
    hsv_img = rgb2hsv(img)

    # get the image's gray scale
    grayScale_img = hsv2rgb(gray_scale(hsv_img))

    # convert the hsv image in int values instead of floating point
    hsv_img = convertTo255(hsv_img)

    # create a mask using the bounds above
    mask = createMaskInRange(hsv_img, lower_bound, upper_bound)

    # create the inverse of the mask above
    invMask = createInvMask(mask)

    # compute the foreground of the image by applying the mask to the gray scale image
    foreground = applyMask(grayScale_img, mask)

    # compute the background of the image by applying the inverse mask to the original image
    background = applyMask(img, invMask)

    # convert the float values in int value in a range [0,255]
    foreground = convertTo255(foreground)

    # compute the final image adding the foreground to the background
    finalImg = background + foreground

    return finalImg 

In [56]:
# take the image in RGB
rocket = ski.data.rocket()
jackets = ski.io.imread("jackets.jpeg")
parrot = ski.io.imread("parrot.jpg")
flowers = ski.io.imread("flowers.jpg")

# set the bounds for the selected color
lowerRed_bound = np.array([240,100,50]) # kinda orange: [10,100,120]
upperRed_bound = np.array([255,255,255]) # kinda orange [39,255,255]

lowerBlue_bound = np.array([120,0,0]) # kinda red: [240,100,50]; kinda orange: [10,100,120]; kinda blue: [140,0,0]; kinda green: [60,0,0] -> [100,0,0]
upperBlue_bound = np.array([180,255,255]) # kinda red: [255,255,255]; kinda orange: [30,255,255] ; kinda blue: [180,255,255]; kinda green: [145,255,255]

lowerGreen_bound = np.array([60,0,0])
upperGreen_bound = np.array([145,255,255])

lowerOrange_bound = np.array([10,100,120])
upperOrange_bound = np.array([30,255,255])

finalJackets = applyFilterToImg(jackets, lowerRed_bound, upperRed_bound)
finalFlowers = applyFilterToImg(flowers, lowerGreen_bound, upperGreen_bound)
finalParrot = applyFilterToImg(parrot, lowerBlue_bound, upperBlue_bound)
finalRocket = applyFilterToImg(rocket, lowerBlue_bound, upperBlue_bound)

img = px.imshow(finalJackets)
img.show()

img = px.imshow(finalRocket)
img.show()

img = px.imshow(finalFlowers)
img.show()

img = px.imshow(finalParrot)
img.show()